# Pandas data manipulation

In the previous notebook, we learnt the basic data structures of pandas and how to look at them. In this notebook, we will manipulate them and

In [1]:
import pandas as pd

# Support the exercises
from solutions import run_solution, show_solution

We will enhance our previous analysis to all movies listed in IMDB.

In [2]:
movie_titles = pd.read_parquet("../data/imdb_movie_titles.parquet")
movie_titles.sample(10)

tconst titleType             primaryTitle  \
483363   tt2060483     movie     Batas bilis at babae   
525075   tt2522486   tvMovie                Spartacus   
283870   tt1058602     movie                Dead Rain   
454945  tt18128036     movie                   Sheila   
32577    tt0045780     movie                Forbidden   
352456   tt1316039     movie       Born from the Foot   
192300   tt0337692     movie              On the Road   
128681   tt0201167     movie  Sta sagonia tis Eforias   
13991    tt0022111     movie       The Maltese Falcon   
300685   tt1116966   tvMovie    Trügerisches Paradies   

                  originalTitle  year  runtimeMinutes                   genres  
483363     Batas bilis at babae  1972            <NA>           Action,Western  
525075                Spartacus  1976              93                Adventure  
283870                Dead Rain  2006              45                      War  
454945                   Sheila  2019             182                    Drama  
32577                 Forbidden  1953              85    Crime,Drama,Film-Noir  
352456       Born from the Foot  2009              98                    Crime  
192300              On the Road  2012             124  Adventure,Drama,Romance  
128681  Sta sagonia tis Eforias  1983              84                   Comedy  
13991        The Maltese Falcon  1931              80    Crime,Drama,Film-Noir  
300685    Trügerisches Paradies  2007              43              Documentary

And we will explore it a bit:

In [3]:
movie_titles.dtypes

tconst            string
titleType         string
primaryTitle      string
originalTitle     string
year               Int64
runtimeMinutes     Int64
genres            string
dtype: object

The titleType contains a lot of repeating values:

In [4]:
movie_titles["titleType"].value_counts()

movie      611121
tvMovie    137403
Name: titleType, dtype: Int64

This looks like a good candidate to convert to categorical (using the [`astype`](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.astype.html) method):

In [5]:
movie_titles["titleType"].astype("category")

0           movie
1           movie
2           movie
3           movie
4           movie
           ...   
748519      movie
748520    tvMovie
748521      movie
748522      movie
748523      movie
Name: titleType, Length: 748524, dtype: category
Categories (2, string): [movie, tvMovie]

Perhaps we could the same with genres...

In [6]:
movie_titles["genres"].value_counts()

Drama                          138437
Documentary                    124846
Comedy                          60044
Horror                          15891
Thriller                        15498
                                ...  
Comedy,Romance,Short                1
Crime,Music,Western                 1
Comedy,Sport,Western                1
Action,Documentary,Thriller         1
Action,Crime,Short                  1
Name: genres, Length: 1458, dtype: Int64

The `tconst` column looks like a good candidate for index. We might still want to check that it is unique:

In [7]:
movie_titles.set_index("tconst", verify_integrity=True)

titleType                                       primaryTitle  \
tconst                                                                   
tt0000009     movie                                         Miss Jerry   
tt0000502     movie                                           Bohemios   
tt0000574     movie                        The Story of the Kelly Gang   
tt0000591     movie                                   The Prodigal Son   
tt0000615     movie                                 Robbery Under Arms   
...             ...                                                ...   
tt9916680     movie  De la ilusión al desconcierto: cine colombiano...   
tt9916692   tvMovie                    Teatroteka: Czlowiek bez twarzy   
tt9916706     movie                                    Dankyavar Danka   
tt9916730     movie                                             6 Gunn   
tt9916754     movie                     Chico Albuquerque - Revelações   

                                               originalTitle  year  \
tconst                                                               
tt0000009                                         Miss Jerry  1894   
tt0000502                                           Bohemios  1905   
tt0000574                        The Story of the Kelly Gang  1906   
tt0000591                                  L'enfant prodigue  1907   
tt0000615                                 Robbery Under Arms  1907   
...                                                      ...   ...   
tt9916680  De la ilusión al desconcierto: cine colombiano...  2007   
tt9916692                    Teatroteka: Czlowiek bez twarzy  2015   
tt9916706                                    Dankyavar Danka  2013   
tt9916730                                             6 Gunn  2017   
tt9916754                     Chico Albuquerque - Revelações  2013   

           runtimeMinutes                      genres  
tconst                                                 
tt0000009              45                     Romance  
tt0000502             100                        <NA>  
tt0000574              70  Action,Adventure,Biography  
tt0000591              90                       Drama  
tt0000615            <NA>                       Drama  
...                   ...                         ...  
tt9916680             100                 Documentary  
tt9916692              66                       Drama  
tt9916706            <NA>                      Comedy  
tt9916730             116                        <NA>  
tt9916754              49                 Documentary  

[748524 rows x 6 columns]

## Basic manipulation

### Destructive or non-destructive?

Whenever you perform multiple operations that take you from one DataFrame (or Series) to another one, you can follow one of the distinct approaches (:

- **non-destructive approach**: In each step, you take an original DataFrame and create a new one from it. You can either save the new data structure to a variable or directly perform a new operation on it (binding several such steps in one "pipe-line"). As we recommend this approach, you will see it used in the rest of the workshop frequently.

- **destructive approach**: You have one object, you write directly to it and wherever a method accepts the `inplace` argument, you pass it a `True` value. This is not encourages, especially if your object lives in many cells / functions and it is not always clear in which of potentially many states it is in.

Sometimes the latter approach is more efficient performance-wise (this depends on a concrete situation) but adds heavier cognitive burden on your and your readers' heads. Use it wisely and always limit the changes to one cell or one function.

### Adding (or replacing) a column


In [8]:
# Destructive way
movie_copy = movie_titles.copy()  # We want to operate on a new object.
movie_copy["titleTypeCat"] = movie_titles["titleType"].astype("category")
movie_copy

tconst titleType  \
0       tt0000009     movie   
1       tt0000502     movie   
2       tt0000574     movie   
3       tt0000591     movie   
4       tt0000615     movie   
...           ...       ...   
748519  tt9916680     movie   
748520  tt9916692   tvMovie   
748521  tt9916706     movie   
748522  tt9916730     movie   
748523  tt9916754     movie   

                                             primaryTitle  \
0                                              Miss Jerry   
1                                                Bohemios   
2                             The Story of the Kelly Gang   
3                                        The Prodigal Son   
4                                      Robbery Under Arms   
...                                                   ...   
748519  De la ilusión al desconcierto: cine colombiano...   
748520                    Teatroteka: Czlowiek bez twarzy   
748521                                    Dankyavar Danka   
748522                                             6 Gunn   
748523                     Chico Albuquerque - Revelações   

                                            originalTitle  year  \
0                                              Miss Jerry  1894   
1                                                Bohemios  1905   
2                             The Story of the Kelly Gang  1906   
3                                       L'enfant prodigue  1907   
4                                      Robbery Under Arms  1907   
...                                                   ...   ...   
748519  De la ilusión al desconcierto: cine colombiano...  2007   
748520                    Teatroteka: Czlowiek bez twarzy  2015   
748521                                    Dankyavar Danka  2013   
748522                                             6 Gunn  2017   
748523                     Chico Albuquerque - Revelações  2013   

        runtimeMinutes                      genres titleTypeCat  
0                   45                     Romance        movie  
1                  100                        <NA>        movie  
2                   70  Action,Adventure,Biography        movie  
3                   90                       Drama        movie  
4                 <NA>                       Drama        movie  
...                ...                         ...          ...  
748519             100                 Documentary        movie  
748520              66                       Drama      tvMovie  
748521            <NA>                      Comedy        movie  
748522             116                        <NA>        movie  
748523              49                 Documentary        movie  

[748524 rows x 8 columns]

In [9]:
# Non-destructive way
movie_titles.iloc[:,:2].assign(
    titleTypeCat=movie_titles["titleType"].astype("category"),
    constant=42
).sample()

tconst titleType titleTypeCat  constant
110555  tt0167173     movie        movie        42

The [assign](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.assign.html) method accepts keyword arguments as column names and values passed as the column contents. Note that we can pass a scalar value, it is then written to all cells.

### Adding a new row (and overwriting)

There is no simple non-destructive way of adding a new row (apart from creating a copy and operating on it; or concating two existing DataFrames). Also there is no fundamental difference between adding and overwriting the rows - like with writing to a `dict`.


In [10]:
movies_copy = movie_titles.copy()
movies_copy.loc[999999] = {
    "titleType": "phoneVideo",
    "primaryTitle": "My Pink Fluffy Unicorn Holiday 2022",
    "year": 2022,
    "runtimeMinutes": 5,
    "genres": "#insta:heart:",
}
movies_copy.tail()

tconst   titleType                         primaryTitle  \
748520  tt9916692     tvMovie      Teatroteka: Czlowiek bez twarzy   
748521  tt9916706       movie                      Dankyavar Danka   
748522  tt9916730       movie                               6 Gunn   
748523  tt9916754       movie       Chico Albuquerque - Revelações   
999999       <NA>  phoneVideo  My Pink Fluffy Unicorn Holiday 2022   

                          originalTitle  year  runtimeMinutes         genres  
748520  Teatroteka: Czlowiek bez twarzy  2015              66          Drama  
748521                  Dankyavar Danka  2013            <NA>         Comedy  
748522                           6 Gunn  2017             116           <NA>  
748523   Chico Albuquerque - Revelações  2013              49    Documentary  
999999                             <NA>  2022               5  #insta:heart:

In [11]:
movies_copy = movie_titles.copy()
movies_copy.iloc[-1] = {
    "titleType": "phoneVideo",
    "primaryTitle": "My Pink Fluffy Unicorn Holiday 2022",
    "year": 2022,
    "runtimeMinutes": 5,
    "genres": "#insta:heart:",
}
movies_copy.tail()

tconst   titleType  \
748519  tt9916680       movie   
748520  tt9916692     tvMovie   
748521  tt9916706       movie   
748522  tt9916730       movie   
748523       <NA>  phoneVideo   

                                             primaryTitle  \
748519  De la ilusión al desconcierto: cine colombiano...   
748520                    Teatroteka: Czlowiek bez twarzy   
748521                                    Dankyavar Danka   
748522                                             6 Gunn   
748523                My Pink Fluffy Unicorn Holiday 2022   

                                            originalTitle  year  \
748519  De la ilusión al desconcierto: cine colombiano...  2007   
748520                    Teatroteka: Czlowiek bez twarzy  2015   
748521                                    Dankyavar Danka  2013   
748522                                             6 Gunn  2017   
748523                                               <NA>  2022   

        runtimeMinutes         genres  
748519             100    Documentary  
748520              66          Drama  
748521            <NA>         Comedy  
748522             116           <NA>  
748523               5  #insta:heart:

Writing to one particular cell uses indexers in the same way as when reading it.

In [12]:
movies_copy = movie_titles.iloc[:,:3].copy()
movies_copy.loc[748523, "primaryTitle"] = "CHANGED!!!"
movies_copy.tail()

tconst titleType                                       primaryTitle
748519  tt9916680     movie  De la ilusión al desconcierto: cine colombiano...
748520  tt9916692   tvMovie                    Teatroteka: Czlowiek bez twarzy
748521  tt9916706     movie                                    Dankyavar Danka
748522  tt9916730     movie                                             6 Gunn
748523  tt9916754     movie                                         CHANGED!!!

Note that pandas doesn't complain when you want to write to a non-existent column or when you use a string key instead of an integer one. It happily adds a new column and changes the index type!

In [13]:
movies_copy = movie_titles.iloc[:,:3]  # Shorte
movies_copy.loc["748523","primarytitle"] = "ADDED!!!"
movies_copy.tail()

tconst titleType                     primaryTitle primarytitle
748520  tt9916692   tvMovie  Teatroteka: Czlowiek bez twarzy          NaN
748521  tt9916706     movie                  Dankyavar Danka          NaN
748522  tt9916730     movie                           6 Gunn          NaN
748523  tt9916754     movie   Chico Albuquerque - Revelações          NaN
748523       <NA>      <NA>                             <NA>     ADDED!!!

In [14]:
movies_copy = movie_titles.copy()
movies_copy.loc[1:3,["primaryTitle", "originalTitle"]] = "CENSORED"
movies_copy.head()

tconst titleType        primaryTitle       originalTitle  year  \
0  tt0000009     movie          Miss Jerry          Miss Jerry  1894   
1  tt0000502     movie            CENSORED            CENSORED  1905   
2  tt0000574     movie            CENSORED            CENSORED  1906   
3  tt0000591     movie            CENSORED            CENSORED  1907   
4  tt0000615     movie  Robbery Under Arms  Robbery Under Arms  1907   

   runtimeMinutes                      genres  
0              45                     Romance  
1             100                        <NA>  
2              70  Action,Adventure,Biography  
3              90                       Drama  
4            <NA>                       Drama

## Deleting columns and rows

There are basically three ways how to do this (two destructive and one non-destructive way):

- the non-destructive [drop](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.drop.html) method
- the destructive variant of drop with `inplace=True`
- the del statement (rarely used, not shown)

Instead of removing, you can also explicitly select the rows/columns you want.

In [15]:
# Non-destructive drop
movie_titles.drop(columns=["tconst", "titleType"])  # Returns a new object

primaryTitle  \
0                                              Miss Jerry   
1                                                Bohemios   
2                             The Story of the Kelly Gang   
3                                        The Prodigal Son   
4                                      Robbery Under Arms   
...                                                   ...   
748519  De la ilusión al desconcierto: cine colombiano...   
748520                    Teatroteka: Czlowiek bez twarzy   
748521                                    Dankyavar Danka   
748522                                             6 Gunn   
748523                     Chico Albuquerque - Revelações   

                                            originalTitle  year  \
0                                              Miss Jerry  1894   
1                                                Bohemios  1905   
2                             The Story of the Kelly Gang  1906   
3                                       L'enfant prodigue  1907   
4                                      Robbery Under Arms  1907   
...                                                   ...   ...   
748519  De la ilusión al desconcierto: cine colombiano...  2007   
748520                    Teatroteka: Czlowiek bez twarzy  2015   
748521                                    Dankyavar Danka  2013   
748522                                             6 Gunn  2017   
748523                     Chico Albuquerque - Revelações  2013   

        runtimeMinutes                      genres  
0                   45                     Romance  
1                  100                        <NA>  
2                   70  Action,Adventure,Biography  
3                   90                       Drama  
4                 <NA>                       Drama  
...                ...                         ...  
748519             100                 Documentary  
748520              66                       Drama  
748521            <NA>                      Comedy  
748522             116                        <NA>  
748523              49                 Documentary  

[748524 rows x 5 columns]

In [16]:
# Destructive drop
movies_copy = movie_titles.copy()
movies_copy.drop(columns=["tconst", "titleType"], inplace=True)  # Returns None
movies_copy

primaryTitle  \
0                                              Miss Jerry   
1                                                Bohemios   
2                             The Story of the Kelly Gang   
3                                        The Prodigal Son   
4                                      Robbery Under Arms   
...                                                   ...   
748519  De la ilusión al desconcierto: cine colombiano...   
748520                    Teatroteka: Czlowiek bez twarzy   
748521                                    Dankyavar Danka   
748522                                             6 Gunn   
748523                     Chico Albuquerque - Revelações   

                                            originalTitle  year  \
0                                              Miss Jerry  1894   
1                                                Bohemios  1905   
2                             The Story of the Kelly Gang  1906   
3                                       L'enfant prodigue  1907   
4                                      Robbery Under Arms  1907   
...                                                   ...   ...   
748519  De la ilusión al desconcierto: cine colombiano...  2007   
748520                    Teatroteka: Czlowiek bez twarzy  2015   
748521                                    Dankyavar Danka  2013   
748522                                             6 Gunn  2017   
748523                     Chico Albuquerque - Revelações  2013   

        runtimeMinutes                      genres  
0                   45                     Romance  
1                  100                        <NA>  
2                   70  Action,Adventure,Biography  
3                   90                       Drama  
4                 <NA>                       Drama  
...                ...                         ...  
748519             100                 Documentary  
748520              66                       Drama  
748521            <NA>                      Comedy  
748522             116                        <NA>  
748523              49                 Documentary  

[748524 rows x 5 columns]

In [17]:
# Non-destructive removal of the first 700000 rows
movie_titles.drop(labels=range(0, 700000))

tconst titleType  \
700000  tt7798040     movie   
700001  tt7798090     movie   
700002  tt7798098     movie   
700003  tt7798104     movie   
700004  tt7798110   tvMovie   
...           ...       ...   
748519  tt9916680     movie   
748520  tt9916692   tvMovie   
748521  tt9916706     movie   
748522  tt9916730     movie   
748523  tt9916754     movie   

                                             primaryTitle  \
700000                                        April Fools   
700001                         Ju jue lian kao de xiao zi   
700002                                   Persuasion Rooms   
700003  Heavy Metal: A Mining Disaster in Northern Quebec   
700004                                        Just Fix It   
...                                                   ...   
748519  De la ilusión al desconcierto: cine colombiano...   
748520                    Teatroteka: Czlowiek bez twarzy   
748521                                    Dankyavar Danka   
748522                                             6 Gunn   
748523                     Chico Albuquerque - Revelações   

                                            originalTitle  year  \
700000                                    4-gatsu no baka  2017   
700001                         Ju jue lian kao de xiao zi  1979   
700002                                       Ikna Odalari  2013   
700003  Heavy Metal: A Mining Disaster in Northern Quebec  2004   
700004                                        Just Fix It  2019   
...                                                   ...   ...   
748519  De la ilusión al desconcierto: cine colombiano...  2007   
748520                    Teatroteka: Czlowiek bez twarzy  2015   
748521                                    Dankyavar Danka  2013   
748522                                             6 Gunn  2017   
748523                     Chico Albuquerque - Revelações  2013   

        runtimeMinutes         genres  
700000              91  Drama,Fantasy  
700001            <NA>          Drama  
700002              67    Documentary  
700003              48    Documentary  
700004              25         Comedy  
...                ...            ...  
748519             100    Documentary  
748520              66          Drama  
748521            <NA>         Comedy  
748522             116           <NA>  
748523              49    Documentary  

[48524 rows x 7 columns]

## Arithmetics & string manipulation

Standard arithmetic operators work on numerical columns too. Such operations are typically performed in a vector-like fashion.

In [18]:
movie_titles.assign(
    age=2022 - movie_titles["year"]
).sample(20)

tconst titleType                    primaryTitle  \
728458   tt8992508     movie                  The Wasp Woman   
520615   tt2404818     movie                         Saattai   
512619   tt2301015   tvMovie                  Neito tornissa   
235767   tt0459854   tvMovie   John & Aage: Toppen og bolden   
569558   tt3709798   tvMovie                      SNL Shorts   
158335   tt0261747     movie    Ingiliz Kemal Lawrense karsi   
215535   tt0393832     movie                       Sudarshan   
652992   tt6149892   tvMovie         Kovalyova iz provintsii   
55092    tt0074151     movie                        The Arch   
529932   tt2649800     movie            House Guest Massacre   
416866  tt15476398     movie  La Teoría de los Vidrios Rotos   
441005  tt16918996     movie               Aren't I Reliable   
380689   tt1416766   tvMovie                    Peor es nada   
280077  tt10468104     movie                  The Mojicons 2   
633677   tt5580688     movie                            Hoax   
272199  tt10214620     movie               Masha from Russia   
196161   tt0346977     movie                 Feng liu mi yue   
667389   tt6574606     movie                   Hippies lokal   
322477  tt11963006     movie                        Relative   
485953  tt20834912     movie           Jack Rogers Anonymous   

                         originalTitle  year  runtimeMinutes  \
728458                  The Wasp Woman  <NA>            <NA>   
520615                         Saattai  2012             150   
512619                  Neito tornissa  1982            <NA>   
235767   John & Aage: Toppen og bolden  2005              30   
569558                      SNL Shorts  2014            <NA>   
158335    Ingiliz Kemal Lawrense karsi  1952              87   
215535                       Sudarshan  1928            <NA>   
652992         Kovalyova iz provintsii  1975             124   
55092                      Dong fu ren  1968              94   
529932            House Guest Massacre  2013              71   
416866  La Teoría de los Vidrios Rotos  2021              80   
441005               Aren't I Reliable  2021            <NA>   
380689                    Peor es nada  1990              50   
280077                  The Mojicons 2  2018            <NA>   
633677                            Hoax  2019              96   
272199               Masha from Russia  <NA>            <NA>   
196161                 Feng liu mi yue  1994            <NA>   
667389                   Hippies lokal  1976              96   
322477                        Relative  2022              97   
485953           Jack Rogers Anonymous  <NA>            <NA>   

                      genres   age  
728458         Horror,Sci-Fi  <NA>  
520615          Drama,Family    10  
512619                 Music    40  
235767                Comedy    17  
569558                Comedy     8  
158335         Adventure,War    70  
215535                  <NA>    94  
652992                 Drama    47  
55092                  Drama    54  
529932       Horror,Thriller     9  
416866                Comedy     1  
441005                 Drama     1  
380689                Comedy    32  
280077                  <NA>     4  
633677                Horror     3  
272199                  <NA>  <NA>  
196161                Comedy    28  
667389                Comedy    46  
322477  Comedy,Drama,Romance     0  
485953  Comedy,Drama,Romance  <NA>

**Exercise hour_length**: Calculate the length of movies in hours.

In [19]:
# run_solution("hour_length")
# show_solution("hour_length")

### Universal operation: [`apply`](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.apply.html)

If you want to apply some operation on every row of a DataFrame, or every item of a Series, the `apply` becomes handy:

In [20]:
actors = pd.DataFrame()

### Basic string operations

These are typically accessed using the `.str` "accessor" of the Series like this:
    
- series.str.lower
- series.str.split
- series.str.startswith
- series.str.contains
- ...

More about this here: <https://pandas.pydata.org/docs/user_guide/text.html>

**Exercise pink:** Find all Pink Panther movies. Note that their title does not necessarily start with "Pink"

In [21]:
# is_pink = ...
# movie_titles[is_pink]

In [22]:
# run_solution("pink")
# show_solution("pink")

In [23]:
# String arithmetics work too!
url = "https://www.imdb.com/title/" + movie_titles["tconst"]
movie_titles[["primaryTitle"]].assign(url=url).sample(10)

primaryTitle  \
323673     Easy Rider: The Snowboard Movie   
116088  La fabricatión de meubles curvados   
740839               Minagoroshi no yokujô   
191082                            Vladimir   
422463                         Eyang Putri   
332235                   Barry the Hatchet   
666997              Sous peine d'innocence   
34127               What Every Woman Wants   
687101            The Woolgatherer's Store   
601293                      Gladiator Wars   

                                          url  
323673  https://www.imdb.com/title/tt12013280  
116088   https://www.imdb.com/title/tt0178427  
740839   https://www.imdb.com/title/tt9557550  
191082   https://www.imdb.com/title/tt0334634  
422463  https://www.imdb.com/title/tt15725158  
332235  https://www.imdb.com/title/tt12351110  
666997   https://www.imdb.com/title/tt6562614  
34127    https://www.imdb.com/title/tt0047671  
687101   https://www.imdb.com/title/tt7313398  
601293   https://www.imdb.com/title/tt4601740

Let's investigate the genres a bit:

In [24]:
split_genres = movie_titles.genres.str.split(",").dropna()
split_genres.sample(10)

703879                          [Comedy]
641948                     [Documentary]
500773                 [Comedy, Romance]
600391            [Comedy, Drama, Music]
374164                          [Action]
2388                             [Drama]
556715                           [Drama]
523845    [Documentary, Family, History]
391640                          [Comedy]
440637                           [Drama]
Name: genres, dtype: object

In [42]:
movie_titles_with_genre_count = movie_titles.assign(
    split_genres = movie_titles["genres"].fillna("").str.split(","),
    genre_count = lambda df: df["split_genres"].apply(lambda item: len(item)).where(df["genres"].notna(), 0)
)
movie_titles_with_genre_count.sample(10)

tconst titleType                             primaryTitle  \
347448   tt1297297     movie                         Rock n Roll Nerd   
150879   tt0248479     movie                Ping bu qing yun shang ji   
560908   tt3511524     movie  Untitled Crispin Hellion Glover Project   
315698  tt11717658     movie                                 Overtown   
52731    tt0071097   tvMovie                    Abschied vom Abschied   
153741   tt0253790     movie                             Tarzan Rifki   
41162    tt0056340     movie                            Scorched Skin   
396436  tt14706804     movie                   Irezumi satsujin jiken   
65449    tt0087348     movie      Goldy: The Last of the Golden Bears   
510410   tt2266781     movie                         Magical Universe   

                                  originalTitle  year  runtimeMinutes  \
347448                         Rock n Roll Nerd  2008              89   
150879                Ping bu qing yun shang ji  1959            <NA>   
560908  Untitled Crispin Hellion Glover Project  <NA>            <NA>   
315698                                 Overtown  <NA>            <NA>   
52731                     Abschied vom Abschied  1974            <NA>   
153741                             Tarzan Rifki  1986              83   
41162                                Pelle viva  1962              98   
396436                   Irezumi satsujin jiken  1953             106   
65449       Goldy: The Last of the Golden Bears  1984              91   
510410                         Magical Universe  2013              80   

                              genres                      split_genres  \
347448  Biography,Comedy,Documentary  [Biography, Comedy, Documentary]   
150879                          <NA>                                []   
560908                         Drama                           [Drama]   
315698                         Drama                           [Drama]   
52731                          Drama                           [Drama]   
153741                  Comedy,Crime                   [Comedy, Crime]   
41162                          Drama                           [Drama]   
396436                          <NA>                                []   
65449               Adventure,Family               [Adventure, Family]   
510410         Biography,Documentary          [Biography, Documentary]   

        genre_count  
347448            3  
150879            0  
560908            1  
315698            1  
52731             1  
153741            2  
41162             1  
396436            0  
65449             2  
510410            2

### Basic statistics

In [26]:
movie_titles["year"].describe()

count    662337.000000
mean       1991.605895
std          28.507317
min        1894.000000
25%        1974.000000
50%        2002.000000
75%        2014.000000
max        2029.000000
Name: year, dtype: float64

How many years in total 

In [27]:
movie_titles["runtimeMinutes"].sum() / 365.25 / 1440

78.65890752148452

To whet your visualization appetite and to check that your setup works, let's visualize how many movies were released in different times during the 128-year history of film. This is best represented by a [histogram](https://en.wikipedia.org/wiki/Histogram), a bar plot that shows how many observations fall within certain ranges of some axis - in this case, it counts how many movies have a certain value of the "year" column.

We will cover visualization in depth in the next notebook, so now without much explanation we will create our first plot using the [plotly](https://plotly.com/python/) library. This example also verifies that the installation worked for you.

In [28]:
import plotly.express as px
px.histogram(movie_titles, "year")

In [33]:
px.histogram(movie_titles, "runtimeMinutes", nbins=50)

In [30]:
movie_titles[["year", "runtimeMinutes"]].median()

year              2002.0
runtimeMinutes      87.0
dtype: float64

**Exercise genre_histogram:** Draw a histogram that shows how many movies have no genres, one genre, ... (Hint: reuse the `genre_count` column above)

In [41]:
# run_solution("genre_histogram")
# show_solution("genre_histogram")

## Filtering and comparison

Indexing in pandas Series / DataFrames (`[]`) support also boolean (masked) arrays. These arrays can be obtained by applying boolean operations on data.

You can also use standard **comparison operators** like `<`, `<=`, `==`, `>=`, `>`, `!=`. 

As an example, find all movies from this year:

In [ ]:
is_from_2022 = (movie_titles["startYear"] == 2022)
is_from_2022.sample(10)

6705009    False
6463593    False
8540713    False
7112115     <NA>
6166768    False
3680922    False
5454553    False
8062571    False
8892029    False
6688448     <NA>
Name: startYear, dtype: boolean

Now we can directly apply the boolean mask. (Note: This is no magic. You can construct the mask yourself)

In [ ]:
movie_titles[is_from_2022]

tconst                       primaryTitle  \
117686   tt0120589               A Dangerous Practice   
193052   tt0200940    Over-sexed Rugsuckers from Mars   
254387   tt0265705                           Saurians   
312786   tt0326716                            5-25-77   
384150   tt0400871                           Take Out   
...            ...                                ...   
9174766  tt9893158                           Clowning   
9174767  tt9893160                         No Way Out   
9175140  tt9894000      Twice As Strong: Made of Fire   
9179935  tt9904252  Nice & Naughty, A Christmas Story   
9180112  tt9904648                       The Contrast   

                             originalTitle  startYear  runtimeMinutes  \
117686                A Dangerous Practice       2022             108   
193052     Over-sexed Rugsuckers from Mars       2022              87   
254387                            Saurians       2022              83   
312786                                 '77       2022             132   
384150                            Take Out       2022            <NA>   
...                                    ...        ...             ...   
9174766                           Clowning       2022              96   
9174767                         No Way Out       2022              89   
9175140      Twice As Strong: Made of Fire       2022             122   
9179935  Nice & Naughty, A Christmas Story       2022            <NA>   
9180112                       The Contrast       2022              82   

                        genres  
117686                   Drama  
193052           Comedy,Sci-Fi  
254387           Action,Sci-Fi  
312786            Comedy,Drama  
384150                  Comedy  
...                        ...  
9174766          Crime,Romance  
9174767  Action,Crime,Thriller  
9175140                  Drama  
9179935   Comedy,Drama,Fantasy  
9180112                 Comedy  

[14655 rows x 6 columns]

It is possible to perform **logical operators** with boolean series too. But note that `and`, `or`, `not` are keywords. You should use `&`, `|` and `~` instead (as overloaded bit operators).

So perhaps we want to list all comedies longer than 3 hours?

In [ ]:
is_a_long_comedy = (movie_titles["runtimeMinutes"] > 180) & (movie_titles["genres"].str.contains("Comedy"))
movie_titles[is_a_long_comedy].sample(10)

tconst                                       primaryTitle  \
134279    tt0138280                                     Tre per sempre   
3776650  tt15121776  Playing Earthbound with one hand holding a tom...   
4146569   tt1579931                                          Bahumathi   
116589    tt0119424                                    Jours de colère   
5446933  tt21233332                         Smosh: Under the Influence   
5005796  tt19263772       UGK David's Sit Down Stand-Up Comedy Special   
2163105  tt12146282                                        Gengsi Dong   
150753    tt0155567                                       Buddimantudu   
25967     tt0026435            Tailspin Tommy in the Great Air Mystery   
74055     tt0075669                                 Amar Akbar Anthony   

                                             originalTitle  startYear  \
134279                                      Tre per sempre       1998   
3776650  Playing Earthbound with one hand holding a tom...       2021   
4146569                                          Bahumathi       2007   
116589                                     Jours de colère       1997   
5446933                         Smosh: Under the Influence       2022   
5005796       UGK David's Sit Down Stand-Up Comedy Special       2022   
2163105                                        Gengsi Dong       1980   
150753                                        Buddimantudu       1969   
25967              Tailspin Tommy in The Great Air Mystery       1935   
74055                                   Amar Akbar Anthony       1977   

         runtimeMinutes                   genres  
134279              200             Comedy,Drama  
3776650             361                   Comedy  
4146569             194                   Comedy  
116589              182   Biography,Comedy,Drama  
5446933             238                   Comedy  
5005796             181                   Comedy  
2163105             196                   Comedy  
150753              187      Action,Comedy,Drama  
25967               236  Action,Adventure,Comedy  
74055               184      Action,Comedy,Drama

We may wonder why we have two title-ish columns: originalTitle and primaryTitle.

In [ ]:
different_title = (movie_titles["originalTitle"] != movie_titles["primaryTitle"])
different_title.name = "Different title"   # Series can have names (Note: DataFrames can't)
different_title.value_counts()

False    533888
True      76356
Name: Different title, dtype: Int64

In [ ]:
# Show just the ones
movie_titles[different_title].sample(10)

tconst                   primaryTitle  \
366703    tt0382586                 Beating a Drum   
32269     tt0032865                       Passione   
6189626   tt3259302                 The Bitter Sea   
5871816   tt2498020             Under the Umbrella   
66615     tt0068004                The Shadow Whip   
1693507  tt11301882             Choosi Choodangane   
315987    tt0330030                   Red Cherry 4   
2739243  tt13218916  We Wanted to Change the World   
55803     tt0056905                Les Carabiniers   
1677912  tt11273780             The American Dream   

                         originalTitle  startYear  runtimeMinutes  \
366703                Bukchineun yeoja       1987              86   
32269                    Oltre l'amore       1940              96   
6189626                          Kuhai       1934            <NA>   
5871816                  Kasa no shita       2012             108   
66615                Ying zi shen bian       1971              78   
1693507            Choosi Choodangaane       2020             113   
315987                 Balgan aengdu 4       1988              95   
2739243  Mes gribejam izmainit pasauli       2020              66   
55803                  Les carabiniers       1963              75   
1677912                     Giac Mo My       2017             103   

                       genres  
366703               Thriller  
32269                   Drama  
6189626                 Drama  
5871816  Drama,Family,Romance  
66615            Action,Drama  
1693507               Romance  
315987                   <NA>  
2739243     Documentary,Music  
55803        Comedy,Drama,War  
1677912         Drama,Romance

**Exercise qe2_reign**: What percentage of movies was shot during the reign of Queen Elizabeth II? Note: Consider only whole years.

In [ ]:
reign_start = 1952
reign_end = 2022


# run_solution("qe2_reign")
# show_solution("qe2_reign")

0.7806777070608291

**Exercise binge_watch**: If you started watching the movies released last year today, no breaks, no sleep, would you be able to finish by Xmas this year? Or the next one? when would it be? (Hint: you can use the [TimeDelta](https://pandas.pydata.org/docs/reference/api/pandas.Timedelta.html) pandas class for date arithmetics).

In [ ]:
# run_solution("binge_watch")
# show_solution("binge_watch")

datetime.datetime(2024, 12, 23, 0, 30, 27, 398013)

## Sorting

Previously, we were sorting by index (using the `sort_index` method). It is also possible sort by values (or by arbitrary expressions)

In [ ]:
# Display 5 longest movies 
movie_titles.sort_values("runtimeMinutes", ascending=False).head()

tconst                     primaryTitle  \
8428894   tt8273150                        Logistics   
6447115   tt3854496                         Ambiancé   
2233947  tt12277054  Carnets Filmés (Liste Complète)   
5937444   tt2659636             Modern Times Forever   
1438453  tt10844900                               Qw   

                           originalTitle  startYear  runtimeMinutes  \
8428894                        Logistics       2012           51420   
6447115                         Ambiancé       2020           43200   
2233947  Carnets Filmés (Liste Complète)       2019           28643   
5937444             Modern Times Forever       2011           14400   
1438453                               Qw       2019           10062   

              genres  
8428894  Documentary  
6447115  Documentary  
2233947  Documentary  
5937444  Documentary  
1438453        Drama

In [ ]:
# Alternative
movie_titles.nlargest(5, "runtimeMinutes")

tconst                     primaryTitle  \
8428894   tt8273150                        Logistics   
6447115   tt3854496                         Ambiancé   
2233947  tt12277054  Carnets Filmés (Liste Complète)   
5937444   tt2659636             Modern Times Forever   
1438453  tt10844900                               Qw   

                           originalTitle  startYear  runtimeMinutes  \
8428894                        Logistics       2012           51420   
6447115                         Ambiancé       2020           43200   
2233947  Carnets Filmés (Liste Complète)       2019           28643   
5937444             Modern Times Forever       2011           14400   
1438453                               Qw       2019           10062   

              genres  
8428894  Documentary  
6447115  Documentary  
2233947  Documentary  
5937444  Documentary  
1438453        Drama

In [ ]:
# Sort by multiple columns
movie_titles.dropna().sort_values(["year", "runtimeMinutes"])

tconst titleType  \
0        tt0000009     movie   
506683   tt2210499     movie   
141833   tt0230366     movie   
161214   tt0266894     movie   
172978   tt0291338     movie   
...            ...       ...   
674753   tt6857072     movie   
721424   tt8712626     movie   
667739   tt6587046     movie   
446768  tt17371536     movie   
405305  tt15060386     movie   

                                             primaryTitle  \
0                                              Miss Jerry   
506683                                         Birmingham   
141833                           Jeffries-Sharkey Contest   
161214                 The Republican National Convention   
172978                                     May Day Parade   
...                                                   ...   
674753                           Bonhoeffer: Holy Traitor   
721424                                                  b   
667739                                   How Do You Live?   
446768  King of Kuzaki Kingdom Life in Soviet Atlassia...   
405305                                       Old Nick III   

                                            originalTitle  year  \
0                                              Miss Jerry  1894   
506683                                         Birmingham  1896   
141833                           Jeffries-Sharkey Contest  1899   
161214                 The Republican National Convention  1900   
172978                                     May Day Parade  1900   
...                                                   ...   ...   
674753                           Bonhoeffer: Holy Traitor  2025   
721424                                                  b  2025   
667739                           Kimitachi wa dô ikiru ka  2026   
446768  King of Kuzaki Kingdom Life in Soviet Atlassia...  2026   
405305                                         Old Nick 3  2027   

        runtimeMinutes                      genres  
0                   45                     Romance  
506683              61                 Documentary  
141833             135      Documentary,News,Sport  
161214              53                 Documentary  
172978              66            Documentary,News  
...                ...                         ...  
674753             130   Adventure,Biography,Drama  
721424             144               Action,Sci-Fi  
667739             125  Adventure,Animation,Family  
446768             167                     Romance  
405305             360                    Thriller  

[444012 rows x 7 columns]

**Exercise 10_oldest:** Find the 10 oldest movies that are longer than 2 hours.

In [ ]:
# run_solution("10_oldest")
# show_solution("10_oldest")

**Exercise longest_title:** Show the row with the movie having the longest (primary) title.

Hint: `idxmax()` method on the Series returns the index of the item with the maximum value. You can't (at least should) not use the maximum value itself.

In [ ]:
# run_solution("longest_title")
# show_solution("longest_title")

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=234de414-c5f7-4e4d-a314-25100ac19112' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>